<a href="https://colab.research.google.com/github/leoarjo/leoarjo/blob/main/aih_municipios_abril_2023.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Análise dos dados das AIH dos Municípios em abril de 2023

Este notebook apresenta uma análise dos dados de Autorizações de Internação Hospitalar (AIH) dos municípios em abril de 2023. Os dados foram obtidos do portal de Informações de Saúde do DATASUS, disponível em https://datasus.saude.gov.br/informacoes-de-saude-tabnet/.

Antes de iniciar a análise neste notebook, realizei uma limpeza preliminar dos dados usando o Excel para garantir que os dados estejam no formato correto e livres de inconsistências.

Nas próximas seções, iremos importar as bibliotecas necessárias, carregar os dados e realizar a análise exploratória.

Dentro desta análise, procurei responder as seguintes perguntas:

1. Existe alguma relação entre a quantidade total e o valor total investido por Unidade da Federação?
2. Qual foi o procedimento mais frequente em abril de 2023?
3. Quais foram os procedimentos mais caros neste período?
4. Quais foram os municípios que mais gastaram com procedimentos de saúde?

Autor: Leonardo Araujo



## Importação das bibliotecas, carga e verificação dos dados

### Bibliotecas

In [ ]:
import psycopg2                     # para conectar ao banco de dados
import pandas as pd                 # para limpeza e manipulação de dataframes
import plotly.express as px         # para plotar gráficos
import plotly.graph_objects as go   # para fazer o gráfico de pizza e de dispersão
import folium                       # para criar o mapa
from IPython.display import display # para mostrar o mapa no notebook
from decimal import Decimal         # para converter facilmente para decimais

### Conexão do banco de dados

In [ ]:
conn = psycopg2.connect(dbname='2312120017_Leonardo', user='2312120017_Leonardo', password='2312120017_Leonardo', host='dataiesb.iesbtech.com.br', port='5432')

### Verificando a conexão e conhecendo a tabela

In [ ]:
cur = conn.cursor()

sql_query = "SELECT * FROM aih_municipios_abril_2023"

df = pd.read_sql_query(sql_query, conn)

df.sample(5)

# ­

<ipython-input-61-7407452708d5>:5: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



ano mes       nome_municipio codigo_municipio_dv  \
554   2023  4                BAIXIO              230180   
2066  2023  4   PATROCINIO PAULISTA              353630   
1175  2023  4               IGAPORA              291340   
2122  2023  4   SANTANA DE PARNAIBA              354730   
294   2023  4                 PEIXE              171660   

      qtd_01_acoes_de_promocao_e_prevencao_em_saude  \
554                                             NaN   
2066                                            NaN   
1175                                            NaN   
2122                                            NaN   
294                                             NaN   

      qtd_02_procedimentos_com_finalidade_diagnostica  \
554                                               NaN   
2066                                            694.0   
1175                                              6.0   
2122                                           3417.0   
294                                              81.0   

      qtd_03_procedimentos_clinicos  qtd_04_procedimentos_cirurgicos  \
554                             6.0                              NaN   
2066                          391.0                            113.0   
1175                           36.0                              5.0   
2122                         2975.0                            111.0   
294                            23.0                              8.0   

      qtd_05_transplantes_de_orgaos_tecidos_e_celulas  qtd_06_medicamentos  \
554                                               NaN                  NaN   
2066                                              NaN                  1.0   
1175                                              NaN                  NaN   
2122                                              NaN                  NaN   
294                                               NaN                  NaN   

      ...  qtd_08_acoes_complementares_da_atencao_a_saude  qtd_total  \
554   ...                                             7.0         13   
2066  ...                                           222.0       1422   
1175  ...                                            82.0        129   
2122  ...                                             NaN       6503   
294   ...                                             NaN        112   

      vl_02_procedimentos_com_finalidade_diagnostica  \
554                                              NaN   
2066                                          866.67   
1175                                             NaN   
2122                                          728.05   
294                                            62.15   

      vl_03_procedimentos_clinicos  vl_04_procedimentos_cirurgicos  \
554                        2914.92                             NaN   
2066                      26136.43                        11142.84   
1175                      15610.41                         3506.55   
2122                      75037.86                        28504.23   
294                        3211.71                         5148.71   

      vl_05_transplantes_de_orgaos_tecidos_e_celulas  vl_06_medicamentos  \
554                                              NaN                 NaN   
2066                                             NaN               93.28   
1175                                             NaN                 NaN   
2122                                             NaN                 NaN   
294                                              NaN                 NaN   

      vl_07_orteses_proteses_e_materiais_especiais  \
554                                            NaN   
2066                                        764.34   
1175                                           NaN   
2122                                           NaN   
294                                            NaN   

      vl_08_acoes_complementares_da_atencao_a_saude   vl_total  
554                                   

In [ ]:
print(df.columns)

Index(['ano', 'mes', 'nome_municipio', 'codigo_municipio_dv',
       'qtd_01_acoes_de_promocao_e_prevencao_em_saude',
       'qtd_02_procedimentos_com_finalidade_diagnostica',
       'qtd_03_procedimentos_clinicos', 'qtd_04_procedimentos_cirurgicos',
       'qtd_05_transplantes_de_orgaos_tecidos_e_celulas',
       'qtd_06_medicamentos', 'qtd_07_orteses_proteses_e_materiais_especiais',
       'qtd_08_acoes_complementares_da_atencao_a_saude', 'qtd_total',
       'vl_02_procedimentos_com_finalidade_diagnostica',
       'vl_03_procedimentos_clinicos', 'vl_04_procedimentos_cirurgicos',
       'vl_05_transplantes_de_orgaos_tecidos_e_celulas', 'vl_06_medicamentos',
       'vl_07_orteses_proteses_e_materiais_especiais',
       'vl_08_acoes_complementares_da_atencao_a_saude', 'vl_total'],
      dtype='object')


In [ ]:
df.describe()

qtd_01_acoes_de_promocao_e_prevencao_em_saude  \
count                                      28.000000   
mean                                        8.285714   
std                                        14.352331   
min                                         1.000000   
25%                                         1.000000   
50%                                         2.500000   
75%                                         9.750000   
max                                        73.000000   

       qtd_02_procedimentos_com_finalidade_diagnostica  \
count                                     2.454000e+03   
mean                                      7.133146e+03   
std                                       4.322094e+04   
min                                       1.000000e+00   
25%                                       9.125000e+01   
50%                                       4.250000e+02   
75%                                       2.283750e+03   
max                                       1.611185e+06   

       qtd_03_procedimentos_clinicos  qtd_04_procedimentos_cirurgicos  \
count                    3039.000000                      2011.000000   
mean                     4034.533070                       499.952760   
std                     23658.081885                      1987.851774   
min                         1.000000                         1.000000   
25%                        43.000000                        20.000000   
50%                       204.000000                        71.000000   
75%                      1173.000000                       259.000000   
max                    786164.000000                     40811.000000   

       qtd_05_transplantes_de_orgaos_tecidos_e_celulas  qtd_06_medicamentos  \
count                                       168.000000           685.000000   
mean                                        220.767857           330.764964   
std                                         743.529888          1911.045616   
min                                           1.000000             1.000000   
25%                                           7.750000             3.000000   
50%                                          20.000000            13.000000   
75%                                          68.750000            73.000000   
max                                        6846.000000         31623.000000   

       qtd_07_orteses_proteses_e_materiais_especiais  \
count                                     807.000000   
mean                                      316.743494   
std                                      1030.768661   
min                                         1.000000   
25%                                        10.000000   
50%                                        44.000000   
75%                                       175.000000   
max                                     16525.000000   

       qtd_08_acoes_complementares_da_atencao_a_saude     qtd_total  \
count                                     2486.000000  3.050000e+03   
mean                                      1529.802092  1.150613e+04   
std                                       7705.560808  7.067640e+04   
min                                          1.000000  1.000000e+00   
25%                                         68.000000  1.470000e+02   
50%                                        204.500000  6.920000e+02   
75%                                        691.500000  3.295500e+03   
max                                     168241.000000  2.661404e+06   

       vl_02_procedimentos_com_finalidade_diagnostica  \
count                                    1.659000e+03   
mean                                     4.971610e+04   
std                                      2.518445e+05   
min                                      1.000000e+00   
25%                                      9.680000e+01   
50%                                      1.104330e+03   
75%                                      1.500061e+04   
max     

### Criação de um dicionário no Python para renomear os atributos

In [ ]:
tipo_procedimento_map_vl = {
    'vl_02_procedimentos_com_finalidade_diagnostica': 'Procedimentos com Finalidade Diagnóstica',
    'vl_03_procedimentos_clinicos': 'Procedimentos Clínicos',
    'vl_04_procedimentos_cirurgicos': 'Procedimentos Cirúrgicos',
    'vl_05_transplantes_de_orgaos_tecidos_e_celulas': 'Transplantes de Órgãos, Tecidos e Células',
    'vl_06_medicamentos': 'Medicamentos',
    'vl_07_orteses_proteses_e_materiais_especiais': 'Órteses, Próteses e Materiais Especiais',
    'vl_08_acoes_complementares_da_atencao_a_saude': 'Ações Complementares da Atenção à Saúde'
}

tipo_procedimento_map_qtd = {
    'qtd_01_acoes_de_promocao_e_prevencao_em_saude': 'Ações de Promoção e Prevenção em Saúde',
    'qtd_02_procedimentos_com_finalidade_diagnostica': 'Procedimentos com Finalidade Diagnóstica',
    'qtd_03_procedimentos_clinicos': 'Procedimentos Clínicos',
    'qtd_04_procedimentos_cirurgicos': 'Procedimentos Cirúrgicos',
    'qtd_05_transplantes_de_orgaos_tecidos_e_celulas': 'Transplantes de Órgãos, Tecidos e Células',
    'qtd_06_medicamentos': 'Medicamentos',
    'qtd_07_orteses_proteses_e_materiais_especiais': 'Órteses, Próteses e Materiais Especiais',
    'qtd_08_acoes_complementares_da_atencao_a_saude': 'Ações Complementares da Atenção à Saúde'
}

## Análise exploratória

### 1. Valor total x Quantidade total por Unidade da Federação


In [ ]:
# Consultas SQL
consulta_valor_total = """
SELECT vl_total, m.uf
FROM aih_municipios_abril_2023 ama
JOIN municipio m ON ama.codigo_municipio_dv = CAST(m.codigo_municipio_dv AS CHAR(6))
GROUP BY ama.vl_total, m.uf;
"""

consulta_qtd_total = """
SELECT qtd_total, m.uf
FROM aih_municipios_abril_2023 ama
JOIN municipio m ON ama.codigo_municipio_dv = CAST(m.codigo_municipio_dv AS CHAR(6))
GROUP BY ama.qtd_total, m.uf;
"""

# Ler os dados do banco de dados
df_valor_total = pd.read_sql_query(consulta_valor_total, conn)
df_qtd_total = pd.read_sql_query(consulta_qtd_total, conn)

# Agrupar os dados por estado (uf) e somar os valores
df_valor_total_grouped = df_valor_total.groupby('uf')['vl_total'].sum().reset_index()
df_qtd_total_grouped = df_qtd_total.groupby('uf')['qtd_total'].sum().reset_index()

# Selecionar os top 10 estados com os maiores valores e quantidades
df_valor_total_top10 = df_valor_total_grouped.nlargest(10, 'vl_total')
df_qtd_total_top10 = df_qtd_total_grouped.nlargest(10, 'qtd_total')

# Plotar os gráficos com Plotly
fig_valor_total = px.bar(df_valor_total_top10.sort_values('vl_total', ascending=True),
                         x='uf', y='vl_total',
                         labels={'uf': 'Estado', 'vl_total': 'Valor Total'},
                         title='Top 10 Estados por Valor Total em Abril de 2023')

fig_qtd_total = px.bar(df_qtd_total_top10.sort_values('qtd_total', ascending=True),
                       x='uf', y='qtd_total',
                       labels={'uf': 'Estado', 'qtd_total': 'Quantidade Total'},
                       title='Top 10 Estados por Quantidade Total em Abril de 2023')

# Mostrar os gráficos
fig_valor_total.show()
fig_qtd_total.show()

<ipython-input-65-b01fca1b280c>:17: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.

<ipython-input-65-b01fca1b280c>:18: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



### 1.1. Análise da Correlação entre Valor e Quantidade

#### Consultas SQL

In [ ]:
# Consultas SQL para obter dados por município
consulta_valor_total_municipio = """
SELECT vl_total, m.nome_municipio as municipio
FROM aih_municipios_abril_2023 ama
JOIN municipio m ON ama.codigo_municipio_dv = CAST(m.codigo_municipio_dv AS CHAR(6))
GROUP BY ama.vl_total, m.nome_municipio;
"""

consulta_qtd_total_municipio = """
SELECT qtd_total, m.nome_municipio as municipio
FROM aih_municipios_abril_2023 ama
JOIN municipio m ON ama.codigo_municipio_dv = CAST(m.codigo_municipio_dv AS CHAR(6))
GROUP BY ama.qtd_total, m.nome_municipio;
"""

#### Mostrar o gráfico

In [ ]:
# Ler os dados do banco de dados
df_valor_total_municipio = pd.read_sql_query(consulta_valor_total_municipio, conn)
df_qtd_total_municipio = pd.read_sql_query(consulta_qtd_total_municipio, conn)

# Agrupar os dados por município e somar os valores
df_valor_total_municipio_grouped = df_valor_total_municipio.groupby('municipio')['vl_total'].sum().reset_index()
df_qtd_total_municipio_grouped = df_qtd_total_municipio.groupby('municipio')['qtd_total'].sum().reset_index()

# Combinar os dados de quantidade total e valor total por município
df_combined_municipio = pd.merge(df_valor_total_municipio_grouped, df_qtd_total_municipio_grouped, on='municipio')

# Calcular a correlação de Pearson entre quantidade total e valor total
correlacao = df_combined_municipio['qtd_total'].corr(df_combined_municipio['vl_total'])

# Plotar o gráfico de dispersão com Plotly para mostrar a correlação
fig_correlation_municipio = px.scatter(df_combined_municipio,
                                       x='qtd_total',
                                       y='vl_total',
                                       labels={'qtd_total': 'Quantidade Total', 'vl_total': 'Valor Total (R$)', 'municipio': 'Município'},
                                       title=f'Correlação entre Quantidade Total e Valor Total Investido por Município em Abril de 2023<br>Coeficiente de Correlação: {correlacao:.2f}',
                                       hover_data=['municipio'])

# Atualizar layout para títulos dos eixos
fig_correlation_municipio.update_layout(
    xaxis_title='Quantidade Total',
    yaxis_title='Valor Total (R$)'
)

# Mostrar o gráfico
fig_correlation_municipio.show()

<ipython-input-67-eb51f6d7dc7e>:2: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.

<ipython-input-67-eb51f6d7dc7e>:3: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



Podemos perceber que o coeficiente de correlação de Pearson é de 0,96, indicando uma correlação muito forte entre as variáveis quantidade e valor. Isso significa que, em geral, quanto maior o número de procedimentos clínicos realizados, maior é o valor total necessário para financiá-los.

### 2. Quantidade de procedimentos por tipo

In [ ]:
# Calcula a quantidade total por tipo de procedimento
quantidade_total_por_tipo = {tipo_procedimento_map_qtd[coluna]: df[coluna].sum() for coluna in tipo_procedimento_map_qtd.keys()}

# Ordena os dados por quantidade
quantidade_total_por_tipo_ordenado = dict(sorted(quantidade_total_por_tipo.items(), key=lambda item: item[1]))

# Converte o dicionário ordenado em um DataFrame para facilitar a plotagem com Plotly
df_quantidade_total_por_tipo_ordenado = pd.DataFrame(list(quantidade_total_por_tipo_ordenado.items()), columns=['Tipo de Procedimento', 'Quantidade'])

# Cria o gráfico de barras horizontais com Plotly
fig = px.bar(df_quantidade_total_por_tipo_ordenado,
             x='Quantidade',
             y='Tipo de Procedimento',
             orientation='h',
             labels={'Quantidade': 'Quantidade', 'Tipo de Procedimento': 'Tipo de Procedimento'},
             title='Quantidade de Procedimentos por Tipo em Abril de 2023')

# Formata o eixo x para exibir os números corretamente
fig.update_layout(xaxis_tickformat=',.0f')

# Mostra o gráfico
fig.show()

### 3. Procedimentos mais caros

In [ ]:
valores_procedimentos = df[['vl_02_procedimentos_com_finalidade_diagnostica',
                            'vl_03_procedimentos_clinicos',
                            'vl_04_procedimentos_cirurgicos',
                            'vl_05_transplantes_de_orgaos_tecidos_e_celulas',
                            'vl_06_medicamentos',
                            'vl_07_orteses_proteses_e_materiais_especiais',
                            'vl_08_acoes_complementares_da_atencao_a_saude']].sum().reset_index()

valores_procedimentos.columns = ['Tipo de Procedimento', 'Valor']

# Mapeia os nomes dos tipos de procedimento
valores_procedimentos['Tipo de Procedimento'] = valores_procedimentos['Tipo de Procedimento'].map(tipo_procedimento_map_vl)

# Ordena os valores em ordem crescente
valores_procedimentos = valores_procedimentos.sort_values(by='Valor', ascending=True)

# Cria o gráfico de barras horizontais
fig_bar = px.bar(valores_procedimentos,
                 x='Valor',
                 y='Tipo de Procedimento',
                 orientation='h',
                 labels={'Valor': 'Valor (R$)', 'Tipo de Procedimento': 'Tipo de Procedimento'},
                 title='Distribuição dos Valores dos Procedimentos')

# Formata o eixo x para exibir os números corretamente
fig_bar.update_layout(xaxis_tickformat='R$,.0f')

# Cria o gráfico de pizza
fig_pie = go.Figure(data=[go.Pie(labels=valores_procedimentos['Tipo de Procedimento'],
                                 values=valores_procedimentos['Valor'],
                                 hole=.3,
                                 textinfo='label+percent',
                                 hoverinfo='label+percent+value')])
fig_pie.update_layout(title_text='Distribuição Percentual dos Valores dos Procedimentos')

# Mostra os gráficos
fig_bar.show()
fig_pie.show()

### 4. Municípios que mais gastaram com procedimentos de saúde

In [ ]:
consulta_valor_total_municipio = """
SELECT vl_total, nome_municipio as "Município"
FROM aih_municipios_abril_2023 ama
"""
df = pd.read_sql_query(consulta_valor_total_municipio, conn)

# Filtrando os top 10 municípios que mais gastaram
top_10_municipios = df.sort_values('vl_total', ascending=False).head(10)

top_10_municipios = top_10_municipios.sort_values('vl_total', ascending=True)

# Criando o gráfico de barras
fig = px.bar(top_10_municipios, x='Município', y='vl_total', title='Top 10 Municípios que Mais Gastaram')

# Mostrando o gráfico
fig.show()

<ipython-input-79-44c1e0f531f0>:5: UserWarning:

pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.



In [ ]:
# Consulta SQL para obter latitude, longitude e valor total
sql_query = """
SELECT m.latitude, m.longitude, aih.vl_total
FROM aih_municipios_abril_2023 aih
JOIN municipio m ON aih.codigo_municipio_dv = CAST(m.codigo_municipio_dv AS CHAR(6))
"""

cur.execute(sql_query)
resultados = cur.fetchall()

# Criar um mapa Folium centrado no Brasil
mapa = folium.Map(location=[-15.788497, -47.879873], zoom_start=4)

# Definir cor fixa para os marcadores
cor_fixa = '#0077b6'

# Adicionar marcadores para cada município com tamanho proporcional ao valor
for resultado in resultados:
    latitude, longitude, valor = resultado
    latitude = float(latitude)
    longitude = float(longitude)
    valor = float(valor)
    folium.CircleMarker(
        location=[latitude, longitude],
        radius=max(3, min(valor / 1_000_000, 15)),  # Ajustar o tamanho do círculo com base no valor, com tamanho mínimo de 3 e máximo de 15
        popup=f"Valor: R${valor:,.2f}",
        color=cor_fixa,
        fill=True,
        fill_color=cor_fixa
    ).add_to(mapa)

# Exibir o mapa
display(mapa)